In [ ]:
from mined_metric.jupyter.utils.data_access_util import get_experiment_data, chum_summary_stats
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec

# INSTRUCTIONS: run each cell top to bottom. The last cell will create 2 plots and a table of aggregated data.
# To make changes to this template, go to https://jhub.zooxlabs.com/ and open the jauckley folder.

EXPERIMENT_ID = "EXPERIMENT_ID_PLACEHOLDER"

In [ ]:
# Retrieve all experiment data and metadata
exp_data = get_experiment_data(EXPERIMENT_ID)
if "exception" in exp_data:
    print("Invalid data is returned: %s" % exp_data["exception"])

In [ ]:
# Calculate basic Chum URI summary statistics
chum_uris = [d["chum_uri"] for d in exp_data["meta"]]

# Uncomment if desired- these take awhile
# stats = chum_summary_stats(chum_uris)
# print("Average duration of Chum URIs: {:.2f}s".format(stats["avg_duration_s"]))
# print("Vehicles: {}".format(stats["vehicles_included"]))


In [ ]:
# Make list of lookback_times.
lookback_times_list = [entry["lookback_time"] for entry in exp_data["meta"] if entry["type"] == "kTrackerTrajectoryAccuracyMetric"]

# Get sorted unique values.
lookback_times = np.unique(lookback_times_list)
num_lookback_times = len(lookback_times)

In [ ]:
# Compute the combined standard deviation of two groups of data: a and b.
# Ref: https://math.stackexchange.com/questions/2971315/how-do-i-combine-standard-deviations-of-two-groups.
def combinedStdDev(n_a, mean_a, std_dev_a, n_b, mean_b, std_dev_b):
    if n_a + n_b < 2:
        return 0.0
    first_term = ((n_a - 1) * std_dev_a**2 + (n_b - 1) * std_dev_b**2) / (n_a + n_b - 1)
    second_term = (n_a * n_b * (mean_a - mean_b)**2) / ((n_a + n_b) * (n_a + n_b - 1))
    return np.sqrt((first_term + second_term))
    
# Combine the combined mean of two groups of data: a and b.
def combinedMean(n_a, mean_a, n_b, mean_b):
    if n_a + n_b < 1:
        return mean_a
    return (n_a * mean_a + n_b * mean_b) / (n_a + n_b)

In [ ]:
n_lat = np.zeros(num_lookback_times)
n_long = np.zeros(num_lookback_times)

mean_lat_errors = np.zeros(num_lookback_times)
max_lat_errors = np.zeros(num_lookback_times)
std_dev_lat_errors = np.zeros(num_lookback_times)

mean_long_errors = np.zeros(num_lookback_times)
max_long_errors = np.zeros(num_lookback_times)
std_dev_long_errors = np.zeros(num_lookback_times)

# Second pass through entries to calculate aggregated metrics.
for entry in exp_data["meta"]:
    if entry["type"] == "kTrackerTrajectoryAccuracyMetric":
        curr_lookback = entry["lookback_time"]
        curr_idx = np.where(lookback_times == curr_lookback)[0][0]
        
        curr_n_lat = entry["num_lateral_data_points"]
        curr_n_long = entry["num_longitudinal_data_points"]
        curr_mean_lat = 0
        curr_max_lat = 0
        curr_std_dev_lat = 0
        curr_mean_long = 0
        curr_max_long = 0
        curr_std_dev_long = 0
        if curr_n_lat > 0:
            curr_mean_lat = entry["mean_lateral_error"]
            curr_max_lat = entry["max_lateral_error"]
            curr_std_dev_lat = entry["std_dev_lateral_error"]
        if curr_n_long > 0:
            curr_mean_long = entry["mean_longitudinal_error"]
            curr_max_long = entry["max_longitudinal_error"]
            curr_std_dev_long = entry["std_dev_longitudinal_error"]
        
        # Calculate new standard deviation
        std_dev_lat_errors[curr_idx] = combinedStdDev(n_lat[curr_idx], mean_lat_errors[curr_idx], std_dev_lat_errors[curr_idx], curr_n_lat, curr_mean_lat, curr_std_dev_lat)
        std_dev_long_errors[curr_idx] = combinedStdDev(n_long[curr_idx], mean_long_errors[curr_idx], std_dev_long_errors[curr_idx], curr_n_long, curr_mean_long, curr_std_dev_long)
        
        # Calculate new mean.
        mean_lat_errors[curr_idx] = combinedMean(n_lat[curr_idx], mean_lat_errors[curr_idx], curr_n_lat, curr_mean_lat)
        mean_long_errors[curr_idx] = combinedMean(n_long[curr_idx], mean_long_errors[curr_idx], curr_n_long, curr_mean_long)
        
        # Update max.
        max_lat_errors[curr_idx] = max(curr_max_lat, max_lat_errors[curr_idx])
        max_long_errors[curr_idx] = max(curr_max_long, max_long_errors[curr_idx])
        
        # Update number of data points.
        n_lat[curr_idx] += curr_n_lat
        n_long[curr_idx] += curr_n_long

In [ ]:
# Remove fields with no data points for graphs.
no_data_mask_lat = n_lat > 0
no_data_mask_long = n_long > 0
lookback_times_lat_g = lookback_times[no_data_mask_lat]
lookback_times_long_g = lookback_times[no_data_mask_long]
n_lat_g = n_lat[no_data_mask_lat]
n_long_g = n_long[no_data_mask_long]
mean_lat_errors_g = mean_lat_errors[no_data_mask_lat]
max_lat_errors_g = max_lat_errors[no_data_mask_lat]
std_dev_lat_errors_g = std_dev_lat_errors[no_data_mask_lat]
mean_long_errors_g = mean_long_errors[no_data_mask_long]
max_long_errors_g = max_long_errors[no_data_mask_long]
std_dev_long_errors_g = std_dev_long_errors[no_data_mask_long]

# Make lateral error plots.
fig, ax0 = plt.subplots()
ax0.plot(lookback_times_lat_g, max_lat_errors_g, color="teal", marker="o")
ax0.plot(lookback_times_lat_g, mean_lat_errors_g, color="mediumaquamarine", marker="o")
ax0.set_xlabel("Lookback Time [s]")
ax0.set_ylabel("Lateral Error [m]")
ax0.legend(["Max Lateral Error", "Mean Lateral Error"])
ax0.grid()
plt.title('Aggregated Lateral Error vs Lookback Time')
plt.show()

fig, ax1 = plt.subplots()
ax1.plot(lookback_times_lat_g, std_dev_lat_errors_g, color="teal", marker="o")
ax1.set_xlabel("Lookback Time [s]")
ax1.set_ylabel("Lateral Error Standard Deviation [m]")
ax1.grid()
plt.title('Aggregated Lateral Error Standard Deviation vs Lookback Time')
plt.show()

# Make longitudinal error plots.
fig, ax2 = plt.subplots()
ax2.plot(lookback_times_long_g, max_long_errors_g, color="teal", marker="o")
ax2.plot(lookback_times_long_g, mean_long_errors_g, color="mediumaquamarine", marker="o")
ax2.set_xlabel("Lookback Time [s]")
ax2.set_ylabel("Longitudinal Error [m]")
ax2.legend(["Max Longitudinal Error", "Mean Longitudinal Error"])
ax2.grid()
plt.title('Aggregated Longitudinal Error vs Lookback Time')
plt.show()

fig, ax3 = plt.subplots()
ax3.plot(lookback_times_long_g, std_dev_long_errors_g, color="teal", marker="o")
ax3.set_xlabel("Lookback Time [s]")
ax3.set_ylabel("Longitudinal Error Standard Deviation [m]")
ax3.grid()
plt.title('Aggregated Longitudinal Error Standard Deviation vs Lookback Time')
plt.show()

# Tabulate the lateral and longitudinal errors.
fig, ax4 = plt.subplots()
rows = ["Lookback Time [s]", "Number of Lateral Data Points", "Mean Lateral Error [m]", "Max Lateral Error [m]", "Lateral Error Standard Deviation [m]", "Number of Longitudinal Data Points", "Mean Longitudinal Error [m]", "Max Longitudinal Error [m]", "Longitudinal Error Standard Deviation [m]"]
cell_text = []
cell_text.append([x for x in lookback_times])
cell_text.append([int(x) for x in n_lat])
cell_text.append([np.round(x, 4) for x in mean_lat_errors])
cell_text.append([np.round(x, 4) for x in max_lat_errors])
cell_text.append([np.round(x, 4) for x in std_dev_lat_errors])
cell_text.append([int(x) for x in n_long])
cell_text.append([np.round(x, 4) for x in mean_long_errors])
cell_text.append([np.round(x, 4) for x in max_long_errors])
cell_text.append([np.round(x, 4) for x in std_dev_long_errors])

rcolors = plt.cm.BuPu(np.full(len(rows), 0.1))
the_table = ax4.table(cellText=cell_text, rowLabels=rows, rowColours=rcolors, loc='center', cellLoc='center')
the_table.scale(3.0, 2.5)
ax4.axis('tight')
ax4.axis('off')
plt.suptitle('Aggregated Tracker Trajectory Statistics')

plt.show()